# Verge and foliot mechanism

References:

- https://github.com/JuliaReach/ReachabilityModels.jl/issues/52

- https://github.com/SciML/DifferentialEquations.jl/issues/703

## Dependencies

In [1]:
using ReachabilityAnalysis, LinearAlgebra, Plots, IntervalConstraintProgramming, StaticArrays
const IA = IntervalArithmetic

LazySets.set_ztol(Float64, 1e-12)

plotly()

┌ Info: Precompiling ReachabilityAnalysis [1e97bd63-91d1-579d-8e8d-501d2b57c93f]
└ @ Base loading.jl:1278
┌ Info: For saving to png with the Plotly backend PlotlyBase has to be installed.
└ @ Plots /home/mforets/.julia/packages/Plots/vsE7b/src/backends.jl:372


Plots.PlotlyBackend()

## Model parameters

In [2]:
const torque = 1.0
const Ic = 10.0
const Iv = 0.15
const rc = 1.0
const rv = 0.3
const αc = 24.0 * pi/180
const er = 0.05
const nteeth = round(Int, 2pi/αc) # n
const Mv = Iv/rv^2
const Mc = Ic/rc^2
const Gc = Mv*(1 + er)/rc/(Mv + Mc)
const Gv = Mc*(1 + er)/rv/(Mv + Mc)
const αv = Gv*rc/(1-er)*αc/2

p = (torque, Ic);

## Guards

In [3]:
# trigonometric constraints for each m
upper_trig(m) = @constraint $rc*sin(x1 - ($m-1)* ($αc)) - $rv*tan(x2 + $αv/2) == 0
lower_trig(m) = @constraint $rc*sin(($m-1)* ($αc) - x1) - $rv*tan(-x2 + $αv/2) == 0

# domain of x1 for each m
upper_dom_x1(m; p=0) = ((m-1-1/2)*αc .. (m-1+1/2)*αc) + (2p)*pi
lower_dom_x1(m; p=0) = ((m-1-1/2)*αc .. (m-1+1/2)*αc) + (2p-1)*pi

# combined domain of x1 and x2 for each m 
upper_dom(m; p=0) = upper_dom_x1(m, p=p) × (-1 .. 1)
lower_dom(m; p=0) = lower_dom_x1(m, p=p) × (-1 .. 1)

# constraint solver tolerance
ε = 0.05

# upper constraints
U = [pave(upper_trig(m), upper_dom(m, p=0), ε).boundary for m in 1:nteeth]
Uv = [reduce(vcat, vertices_list(B) for B in Ui) |> VPolygon for Ui in U]

# lower constraints
L = [pave(lower_trig(m), lower_dom(m, p=0), ε).boundary for m in 1:nteeth];
Lv = [reduce(vcat, vertices_list(B) for B in Li) |> VPolygon for Li in L];

In [4]:
fig = plot(xlab="x₁", ylab="x₂", title="Collision conditions, blue: upper, red: lower")

plot!(fig, Uv, c=:blue)
plot!(fig, Lv, c=:red)

<!DOCTYPE html>
 
 
 Plots.jl

In [5]:
G34_upper = HalfSpace(SA[-rc, rv], 0.0)   # rc x3 - rv x4 > 0
G34_lower = HalfSpace(SA[-rc, -rv], 0.0); # rc x3 + rv x4 > 0

## Transition map

In [6]:
# σ = 1
Tupper = SA[0 0 0 0 0;
            0 0 0 0 0;
            0 0 -rc*Gc rv*Gc 0;
            0 0 rc*Gv -rv*Gv 0]

# σ = -1
Tlower = SA[0 0 0 0 0;
            0 0 0 0 0;
            0 0 -rc*Gc -rv*Gc 0;
            0 0 -rc*Gv -rv*Gv 0];

## Continuous post-operator

In [7]:
# variables x1, x2, x3, x4 and the last variable x5 wraps the constant input term
A = zeros(5, 5)
A[1, 3] = 1.0
A[2, 4] = 1.0
A[3, 5] = 1.0

X0 = Singleton([0, 0, 0, 3.0, p[1]/p[2]])
prob = @ivp(x' = A*x, x(0) ∈ X0);

In [8]:
#sol = solve(prob, tspan=(0.0, 0.5), alg=GLGM06(δ=1e-3));
sol = solve(prob, tspan=(0.0, 0.5), alg=GLGM06(δ=1e-3, static=true, dim=5, ngens=10, max_order=2))

fp = flowpipe(sol);

In [9]:
# if we use static arrays
#@btime solve($prob, tspan=(0.0, 0.5), alg=GLGM06(δ=1e-3, static=true, dim=5, ngens=10, max_order=2))
#  234.797 μs (229 allocations: 277.86 KiB)

In [10]:
plot(sol, vars=(0, 1), xlab="t", ylab="x₁(t)")

<!DOCTYPE html>
 
 
 Plots.jl

In [11]:
plot(sol, vars=(3, 4), xlab="x₃", ylab="x₄")

<!DOCTYPE html>
 
 
 Plots.jl

In [12]:
fig = plot(xlab="x₁", ylab="x₂", title="Trig constraints (p = 0), blue: upper, red: lower")

plot!(fig, sol, vars=(1, 2), xlab="x₁", ylab="x₂", lw=1.0, alpha=1.0)
plot!(fig, Uv, c=:blue)
plot!(fig, Lv, c=:red)

<!DOCTYPE html>
 
 
 Plots.jl

In [13]:
fig = plot(xlab="x₃", ylab="x₄", xlims=(-10, 10), ylims=(-10, 10))

plot!(fig, G34_upper, lab="Upper", alpha=.4)
plot!(fig, G34_lower, lab="Lower",  alpha=.4)

# see ReachabilityAnalysis#389
# plot!(fig, project(sol, (3, 4)), lw=3.0)
plot!(fig, [project(set(R), (3, 4)) for R in sol], lw=3.0)

<!DOCTYPE html>
 
 
 Plots.jl

## Algorithm

In [14]:
typeof(fp)

Flowpipe{Float64,ReachSet{Float64,Zonotope{Float64,SArray{Tuple{5},Float64,1,5},SArray{Tuple{5,10},Float64,2,50}}},Array{ReachSet{Float64,Zonotope{Float64,SArray{Tuple{5},Float64,1,5},SArray{Tuple{5,10},Float64,2,50}}},1}}

In [15]:
fig = plot(xlab="x₁", ylab="x₂", title="Trig constraints (p = 0), blue: upper, red: lower")

plot!(fig, sol, vars=(1, 2), xlab="x₁", ylab="x₂", lw=1.0, alpha=1.0)

plot!(fig, Uv, c=:blue)
plot!(fig, U[1])

Uv1 = Uv[1];
Uv1 = VPolygon([Vector(vi) for vi in vertices_list(Uv1)])

plot!(fig, Lv, c=:red)
plot!(fig, L[9])
Lv9 = Lv[9];
Lv9 = VPolygon([Vector(vi) for vi in vertices_list(Lv9)])

fig

<!DOCTYPE html>
 
 
 Plots.jl

We consider the problem of intersecting the flowpipe with the guards $L$ and $U$.

In [16]:
using BenchmarkTools

In [17]:
const πM12 = SA[1.0 0 0 0 0; 0 1.0 0 0 0]

# return the indices in the flowpipe fp that intersect any of the guard sets L and U
function jump_indices(F::Flowpipe{N, <:ReachSet{N, ZT}}, L::VPolygon, U::VPolygon) where {N, ZT<:Zonotope{N}}
    VT = Vector{N}
    idx = Vector{Tuple{Int, Symbol, VPolygon{N, VT}}}()

    for (i, R) in enumerate(F)
        
        # πZ = project(Z, (1, 2)) # see RA#391, doesn't work with SArray
        #πZ = linear_map(πM12v, set(R))
        πZ = project(set(R), (1, 2))
        πV = convert(VPolygon, πZ)

        XL = intersection(πV, L)
        if !isempty(XL)
            push!(idx, (i, :L, XL))
        end

        XU = intersection(πV, U)
        if !isempty(XU)
            push!(idx, (i, :U, XU))
        end
    end
    return idx
end

function cluster_polygon(J::Vector{Tuple{Int, Symbol, VPolygon{N, VT}}}) where {N, VT}
    first_idx = first(J)[1]
    last_idx = last(J)[1]

    vall = Vector{VT}()
    for Ji in J
        for vi in vertices_list(Ji[3])
            push!(vall, vi)
        end
    end
    return VPolygon(vall)
end

cluster_polygon (generic function with 1 method)

In [ ]:
# Using naively the disjointness check from LazySets
#
# @btime jump_indices($fp, $Lv9, $Uv1);
#   74.349 ms (609750 allocations: 51.20 MiB)
#
# Choose VPolygon-VPolygon intersection algorithm
# @btime jump_indices($fp, $Lv9, $Uv1);
#   5.281 ms (51852 allocations: 3.63 MiB)

In [27]:
# @btime jump_indices($fp, $Lv9, $Uv1);
J = jump_indices(fp, Lv9, Uv1);
q = cluster_polygon(J)


plot(q)

<!DOCTYPE html>
 
 
 Plots.jl

In [30]:
plot(2.0 * q)
z = overapproximate(q * 2.0, Zonotope, OctDirections(2))
#plot(overapproximate(q, 1e-4))
plot!(z)

<!DOCTYPE html>
 
 
 Plots.jl

In [20]:
overapproximate(q, 1e-3).constraints

4-element Array{HalfSpace{Float64,Array{Float64,1}},1}:
 HalfSpace{Float64,Array{Float64,1}}([1.0, 0.0], 0.004898499999999983)
 HalfSpace{Float64,Array{Float64,1}}([0.0, 1.0], 0.9367328012848368)
 HalfSpace{Float64,Array{Float64,1}}([-1.0, 0.0], -0.004321799999999978)
 HalfSpace{Float64,Array{Float64,1}}([0.0, -1.0], -0.8843305545876525)

In [21]:
plot(q)
plot!(overapproximate(q, Zonotope, CustomDirections([c.a for c in overapproximate(q, 1e-4).constraints])))

<!DOCTYPE html>
 
 
 Plots.jl

In [22]:
qq = VPolygon(vertices_list(overapproximate(q, 1e-6)))

VPolygon{Float64,Array{Float64,1}}([[0.004321799999999978, 0.8844188378610882], [0.0043513000000000865, 0.8843305545876524], [0.004380849999999991, 0.885000000000001], [0.004898499999999983, 0.9360000000000008], [0.004898499999999983, 0.9367328012848368], [0.004867200000000081, 0.9367328012848369], [0.004836049999999982, 0.9360000000000006], [0.00480651561695409, 0.9331671055474732], [0.0046970000000000215, 0.9225000000000093], [0.004561170900069597, 0.9091397606625883], [0.004435429547008363, 0.8965274415185391], [0.004329543105922942, 0.8858138049837705], [0.004321799999999979, 0.8849999999999995]])

In [23]:
qq.vertices

13-element Array{Array{Float64,1},1}:
 [0.004321799999999978, 0.8844188378610882]
 [0.0043513000000000865, 0.8843305545876524]
 [0.004380849999999991, 0.885000000000001]
 [0.004898499999999983, 0.9360000000000008]
 [0.004898499999999983, 0.9367328012848368]
 [0.004867200000000081, 0.9367328012848369]
 [0.004836049999999982, 0.9360000000000006]
 [0.00480651561695409, 0.9331671055474732]
 [0.0046970000000000215, 0.9225000000000093]
 [0.004561170900069597, 0.9091397606625883]
 [0.004435429547008363, 0.8965274415185391]
 [0.004329543105922942, 0.8858138049837705]
 [0.004321799999999979, 0.8849999999999995]

In [24]:
plot(qq)

dirs = CustomDirections([ci.a for ci in constraints_list(tohrep(qq))])

plot!(LazySets.Approximations._overapproximate_zonotope_vrep(qq, dirs))

<!DOCTYPE html>
 
 
 Plots.jl

In [25]:
plot(overapproximate(qq, Zonotope, BoxDiagDirections(2)))

<!DOCTYPE html>
 
 
 Plots.jl

In [26]:
cbdsc
plot!(overapproximate(qq, Zonotope, OctDirections(2)))

<!DOCTYPE html>
 
 
 Plots.jl

In [ ]:
#q = rand(Zonotope)

plot(q)
#plot!(overapproximate(q, Zonotope, BoxDiagDirections(2)))
plot!(qq)

In [ ]:
plot!(overapproximate(q, Zonotope, OctDirections(2)))

In [ ]:
Z = LazySets.Approximations._overapproximate_zonotope_vrep(q, OctDirections(2))

Z.generators

In [ ]:
plot(LazySets.Approximations._overapproximate_zonotope_vrep(q, OctDirections(2)))

In [ ]:
#dirs = CustomDirections([ci.a for ci in constraints_list(tohrep(Lv9))])
dirs = CustomDirections([ci.a for ci in constraints_list(tohrep(q))])
#dirs = PolarDirections(50)
#dirs = OctDirections(2)

s = overapproximate(q, Zonotope, dirs)

plot(q)
plot!(s)

In [ ]:
@btime cluster_polygon($J);

In [ ]:
# find guard's index which intersect the flowpipe
#sol12 = project(sol, (1, 2))

typeof(sol)

In [ ]:
# find guard's index which intersect the flowpipe
sol12 = project(sol, (1, 2))

findall(Gm -> !isdisjoint(sol12, Gm), Lv)

In [ ]:
# using loops
sol12 = project(sol, (1, 2)) # currently returns an array of LazySets
sol12u = UnionSetArray(sol12);

In [ ]:
# find all
@time findall(X -> !isdisjoint(sol12u, X), Lv);

In [ ]:
plot(Lv[9])
plot!(sol, vars=(1, 2))

In [ ]:
findall(X -> !isdisjoint(X, Lv[9]) && !(X ⊆ Lv[9]), array(sol12u))

In [ ]:
plot(Lv[9])
plot!(sol, vars=(1, 2))
plot!(sol[295], vars=(1, 2), c=:black)
plot!(sol[313], vars=(1, 2), c=:black)

In [ ]:
plot(Lv[9])
plot!(sol, vars=(1, 2))
plot!(sol[295], vars=(1, 2), c=:black)
plot!(sol[313], vars=(1, 2), c=:black)
Y = intersection(sol12[295], Lv[9])
plot!(Y)

In [ ]:
plot(Lv[9])
plot!(sol, vars=(1, 2))
plot!(sol[295], vars=(1, 2), c=:black)
plot!(sol[313], vars=(1, 2), c=:black)
Y = intersection(project(sol, (1, 2))[295], Lv[9])
plot!(Y)

Z = overapproximate(Y, Zonotope, OctDirections)
plot!(Z)

In [ ]:
Z = overapproximate(Y, Zonotope, PolarDirections(20))

In [ ]:
plot(Y, lab="Y")
plot!(Z, lab="Z")

In [ ]:
Z.generators

In [ ]:
#overapproximate(sol12[295] ∩ Lv[9], Zonotope) # not working
#overapproximate(sol12[295] ∩ Lv[9], Zonotope, BoxDirections(2)) # not working

In [ ]:
struct Clock{T<:AbstractContinuousSystem, MT, CT, VT} <: AbstractHybridSystem
    fc::T      # continuous system
    fd::MT     # jump function 
    Cupper::CT # collision condition (upper part)
    Clower::CT # collision condition (lower part)
    Vupper::VT # velocities condition (upper part)
    Vlower::VT # lower part
end

In [ ]:
const RA = ReachabilityAnalysis

In [ ]:
# Assumptions:
# 
# - It is assumed that the set representation used in the continuous post-operator is closed under
#   intersection with the guard set.
#
#
function _solve(ivp::I}; tspan, cpost)

    # preallocate output flowpipe
    RT = rsetrep(cpost)
    out = Vector{Flowpipe{N, RT, Vector{RT}}}()

    # initialize waiting list
    X0 = initial_state(ivp)
    STwl = Zonotope{N, Vector{N}}
    waiting_list = WaitingList{TimeInterval, STwl, Int}()
    push!(waiting_list, StateInLocation(X0, 1))
    H = system(ivp)

    # list of (set, loc) tuples which have already been processed
    explored_list = typeof(waiting_list)()

    # elapsed time accumulators
    t0 = tstart(time_span)
    T = tend(time_span)

    # counter for the number of transitions
    count_jumps = 0

    while !isempty(waiting_list)
        (Δt0, elem) = pop!(waiting_list)
        tprev = tstart(Δt0)
        push!(explored_list, elem)

        # compute reachable states by continuous evolution
        X0 = state(elem)
        time_span = TimeInterval(t0, T-tprev)
        F = post(cpost, IVP(S, X0), time_span; Δt0=Δt0, kwargs...)
        push!(out, F)

        # instantiate post_d : X -> (R(X ∩ G ∩ I⁻) ⊕ W) ∩ I⁺
        #discrete_post = DiscreteTransition(H, t)
        #G = guard(discrete_post)

        # find reach-sets that may take the jump
        # jump_rset_idx is a vector of tuples (idx, :guard, X) where X is the concrete intersection
        # of F[idx] and the guard with symbol :guard
        jump_rset_idx = jump_indices(fp, L, U)
        
        # continue if there is no guard enabled for this transition
        isempty(jump_rset_idx) && error("intersection between flowpipe and guard set not detected")

        # apply clustering method to those sets which intersect the guard
        Xc = cluster(F, jump_rset_idx, clustering_method)

            for Xci in Xc
                # compute reachable states by discrete evolution
                X = apply(discrete_post, Xci, intersection_method)

                # do not add empty sets; checking `isempty` generalizes
                isa(X, EmptySet) && continue
                #isempty(X) && continue # though it may have to solve a feasibility LP if X is a polyhedron

                count_jumps += 1

                # check if this location has already been explored;
                # if it is not the case, add it to the waiting list
                r = target(H, t)
                Xr = StateInLocation(X, r)

                hit_max_jumps = count_jumps > max_jumps
                if hit_max_jumps
                    @warn "maximum number of jumps reached; try increasing `max_jumps`"
                end

                if fixpoint_check
                    if !hit_max_jumps && !(Xr ⊆ explored_list)
                        push!(waiting_list, tspan(Xci), Xr)
                    end
                else
                    # We only push the set Xci if it intersects with time_span
                    if !hit_max_jumps && !IA.isdisjoint(tspan(Xci), time_span0)
                        push!(waiting_list, tspan(Xci), Xr)
                    end
                end
            end
        end # for
    end # while

    # wrap the flowpipe and algorithm in a solution structure
    if intersect_source_invariant
        HFout = HybridFlowpipe(out_in_inv)
    else
        HFout = HybridFlowpipe(out)
    end
    sol = ReachSolution(HFout, cpost)
end

In [ ]:
# Assumptions:
# 
# - It is assumed that the set representation used in the continuous post-operator is closed under
#   intersection with the guard set.
#
#
function _solve(ivp::I}; tspan, cpost)

    # preallocate output flowpipe
    RT = rsetrep(cpost)
    out = Vector{Flowpipe{N, RT, Vector{RT}}}()

    # initialize waiting list
    X0 = initial_state(ivp)
    STwl = Zonotope{N, Vector{N}}
    waiting_list = WaitingList{TimeInterval, STwl, Int}()
    push!(waiting_list, StateInLocation(X0, 1))
    H = system(ivp)

    # list of (set, loc) tuples which have already been processed
    explored_list = typeof(waiting_list)()

    # elapsed time accumulators
    t0 = tstart(time_span)
    T = tend(time_span)

    # counter for the number of transitions
    count_jumps = 0

    while !isempty(waiting_list)